In [7]:
import numpy as np
import tensorflow as tf
from tensorflow.keras.layers import Layer
from tensorflow.keras.models import Model, load_model
from tensorflow.keras.layers import Input, LSTM, Dense, Embedding, MultiHeadAttention, LayerNormalization, Add
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from sklearn.model_selection import train_test_split
from collections import Counter
import nbformat
import math
from tensorflow.keras.callbacks import Callback

In [4]:
""" Currently not supported
#from tensorflow.keras.mixed_precision import experimental as mixed_precision

tf.config.experimental.set_virtual_device_configuration(
    tf.config.list_physical_devices('CPU')[0],
    [tf.config.experimental.VirtualDeviceConfiguration(memory_limit=4096)]
)

policy = mixed_precision.Policy('mixed_float16')
mixed_precision.set_policy(policy)
"""

" Currently not supported\n#from tensorflow.keras.mixed_precision import experimental as mixed_precision\n\ntf.config.experimental.set_virtual_device_configuration(\n    tf.config.list_physical_devices('CPU')[0],\n    [tf.config.experimental.VirtualDeviceConfiguration(memory_limit=4096)]\n)\n\npolicy = mixed_precision.Policy('mixed_float16')\nmixed_precision.set_policy(policy)\n"

In [43]:
%run '/home/ec2-user/kaggle/rudolph/dataPrep.ipynb'

Story text extracted successfully:
Story text extracted successfully:
Story text extracted successfully:
Story text extracted successfully:
Story text extracted successfully:
Story text extracted successfully:
Story text extracted successfully:
Story text extracted successfully:
Story text extracted successfully:
Story text extracted successfully:
Story text extracted successfully:
Story text extracted successfully:
Story text extracted successfully:
Story text extracted successfully:
Story text extracted successfully:
Story text extracted successfully:
Story text extracted successfully:
Story text extracted successfully:
Story text extracted successfully:
Story text extracted successfully:
Story text extracted successfully:
Story text extracted successfully:
Story text extracted successfully:
Story text extracted successfully:
Story text extracted successfully:
Story text extracted successfully:
Story text extracted successfully:
Story text extracted successfully:
Story text extracted

In [3]:
print(stories[0][0])
print(stories[0][1])

A Boy was given permission to put his hand into a pitcher to get some filberts. But he took such a great fistful that he could not draw his hand out again. There he stood, unwilling to give up a single filbert and yet unable to get them all out at once. Vexed and disappointed he began to cry.
"My boy," said his mother, "be satisfied with half the nuts you have taken and you will easily get your hand out. Then perhaps you may have some more filberts some other time."
Do not attempt too much at once.



Return to theAesoplibrary , or . . . Read the next short story;The Boy And The Nettle
Or read more short stories for kids in ourChildren's Library
into other to easily out But his theAesoplibrary , Library them great out have There at mother, stories The took you was with hand to may his Boy Nettle your not at boy," and not "My a taken stood, once. said up next filbert once. or began and perhaps fistful Vexed you that too single . more half put he ourChildren's filberts satisfied much . D

In [44]:
# Sample dataset: Pairs of original and scrambled sentences 
"""
sentences = [
    ("I love programming", "programming I love"),
    ("Keras makes deep learning easy", "makes easy Keras deep learning"),
    ("The cat sat on the mat", "on the mat The cat sat"),
    ("Hello world", "world Hello"),
    ("Pine Cone and Pepper Pot ran after her. Jeremy Mouse only stuck his head out of the snow cave. He didn’t want Jack Frost to nip his toes and certainly not his tail! Jack Frost! Jack Frost! cried Tiptoes. We’ve come to pay a visit. Jack Frost landed next to them. He was pale, icy blue, and his arms and fingers were long and glistening. His eyes were sharp, and his wings crackled like breaking ice whenever he moved. He looked so fierce that Pine Cone and Pepper Pot were afraid to open their mouths. It became so chilly they wrapped their beards round their necks and pulled their hats over their ears.", "snow he beards only fingers so out their We’ve of and came his sharp, they Cone her. afraid glistening. he Jack long, their It Jack He open his Pot! was to Pot and hats nip after not He necks the ears. Jeremy over Jack next icy Mouse round moved. He tail! was pale, the pay their icy pine wrapped their didn’t heads ice fierce glistening. mouths. breaking over pay Jack next like arms his moved. and certainly! only out was the look Tiptoes over not mouths. and he his to Pepper afraid cave. him Jeremy stuck crackled came blue, pulled ran his round with tail! He them. Mouse after didn’t nip fingers wings their not tail! mouse Pot afraid stuck arms of toes icy Cone was them pay. Pine wings came Pepper their He fierce long his wings Cone hats icy his over and next certainly Jack after ears. glistening. pay tiptoes! like pine ran was icy cave! certainly moved the."),
    ("Machine learning is fascinating", "fascinating Machine is learning"),
]
"""
sentences = stories

In [45]:
scrambled_sentences = [s[1] for s in sentences]
sequence_lengths = [len(seq) for seq in ((seq.split()) for seq in scrambled_sentences)]
print("Max length:", np.max(sequence_lengths))
print("Mean length:", np.mean(sequence_lengths))
print("25th percentile:", np.percentile(sequence_lengths, 25))
print("50th percentile:", np.percentile(sequence_lengths, 50))
print("95th percentile:", np.percentile(sequence_lengths, 95))
#max_seq_length = int(np.percentile(sequence_lengths, 95))

Max length: 200
Mean length: 193.97306930693068
25th percentile: 200.0
50th percentile: 200.0
95th percentile: 200.0


In [ ]:
#print(sentences[0])
#print(stories[0])


('I love programming', 'programming I love')
('A Boy was given permission to put his hand into a pitcher to get some filberts. But he took such a great fistful that he could not draw his hand out again. There he stood, unwilling to give up a single filbert and yet unable to get them all out at once. Vexed and disappointed he began to cry.\n"My boy," said his mother, "be satisfied with half the nuts you have taken and you will easily get your hand out. Then perhaps you may have some more filberts some other time."\nDo not attempt too much at once.\n\n\n\nReturn to theAesoplibrary , or . . . Read the next short story;The Boy And The Nettle\nOr read more short stories for kids in ourChildren\'s Library', 'into other to easily out But his theAesoplibrary , Library them great out have There at mother, stories The took you was with hand to may his Boy Nettle your not at boy," and not "My a taken stood, once. said up next filbert once. or began and perhaps fistful Vexed you that too single . 

In [46]:
# New Add <start> and <end> tokens to the original sentences because it seems to break the algorithm without them
original_sentences = [f"<start> {s[0]} <end>" for s in sentences]
scrambled_sentences = [s[1] for s in sentences]

# Tokenize and preprocess sentences
tokenizer = Tokenizer(filters="")
tokenizer.fit_on_texts(original_sentences + scrambled_sentences)
word_index = tokenizer.word_index
vocab_size = len(word_index) + 1
"""
max_seq_length = max(
    max(len(seq.split()) for seq in scrambled_sentences),
    max(len(seq.split()) for seq in original_sentences),
)
"""
percentile = 95
max_seq_length = int(np.percentile(sequence_lengths, percentile))
print(f"max seq length for {percentile}th percentile = {max_seq_length}")
# Convert sentences to sequences and pad
input_sequences = pad_sequences(tokenizer.texts_to_sequences(scrambled_sentences), maxlen=max_seq_length, padding="post")
target_sequences = pad_sequences(tokenizer.texts_to_sequences(original_sentences), maxlen=max_seq_length, padding="post")

# Create target sequences for teacher forcing
target_input_sequences = target_sequences[:, :-1]
target_output_sequences = target_sequences[:, 1:]



max seq length for 95th percentile = 200


In [47]:
class PositionalEncoding(tf.keras.layers.Layer):
    def __init__(self, max_position, embed_dim, **kwargs):
        super(PositionalEncoding, self).__init__(**kwargs)
        self.max_position = max_position
        self.embed_dim = embed_dim
        self.pos_encoding = self._get_positional_encoding(max_position, embed_dim)

    def _get_positional_encoding(self, position, d_model):
        """
        Generate a matrix of positional encodings.
        """
        angle_rads = self._get_angles(np.arange(position)[:, np.newaxis],
                                      np.arange(d_model)[np.newaxis, :],
                                      d_model)

        # Apply sin to even indices in the array
        angle_rads[:, 0::2] = np.sin(angle_rads[:, 0::2])

        # Apply cos to odd indices in the array
        angle_rads[:, 1::2] = np.cos(angle_rads[:, 1::2])

        pos_encoding = angle_rads[np.newaxis, ...]

        return tf.cast(pos_encoding, dtype=tf.float32)

    def _get_angles(self, pos, i, d_model):
        """
        Compute angles for the positional encoding matrix.
        """
        angle_rates = 1 / np.power(10000, (2 * (i // 2)) / np.float32(d_model))
        return pos * angle_rates

    def call(self, inputs):
        """
        Add positional encoding to the input tensor.
        """
        seq_len = tf.shape(inputs)[1]
        return inputs + self.pos_encoding[:, :seq_len, :]

    def compute_output_shape(self, input_shape):
        """
        Ensure the output shape matches the input shape.
        """
        return input_shape


In [67]:


embedding_dim = 256 #150 #120 #100
latent_dim = 256 #120 #100
num_heads = 8 #4

# Encoder
encoder_inputs = Input(shape=(max_seq_length,))
encoder_embedding = Embedding(vocab_size, embedding_dim)(encoder_inputs)
positional_encoding = PositionalEncoding(max_seq_length, embedding_dim)(encoder_embedding)
#encoder_outputs = Dense(latent_dim)(encoder_embedding)
encoder_outputs = Dense(latent_dim)(positional_encoding)

# Additional encoder layer
encoder_dense_2 = Dense(latent_dim, activation="relu")(encoder_outputs)
encoder_outputs = Add()([encoder_outputs, encoder_dense_2])  # Residual connection
encoder_outputs = LayerNormalization()(encoder_outputs)


# Decoder
decoder_inputs = Input(shape=(max_seq_length - 1,))
decoder_embedding = Embedding(vocab_size, embedding_dim)(decoder_inputs)
decoder_positional_encoding = PositionalEncoding(max_seq_length - 1, embedding_dim)(decoder_embedding)

# Self-Attention
decoder_self_attention = MultiHeadAttention(num_heads=num_heads, key_dim=latent_dim)(decoder_embedding, decoder_embedding)
decoder_self_attention = Add()([decoder_embedding, decoder_self_attention])
decoder_self_attention = LayerNormalization()(decoder_self_attention)

# Cross-Attention
decoder_cross_attention = MultiHeadAttention(num_heads=num_heads, key_dim=latent_dim)(decoder_self_attention, encoder_outputs)
decoder_cross_attention = Add()([decoder_self_attention, decoder_cross_attention])
decoder_cross_attention = LayerNormalization()(decoder_cross_attention)

# Feed-forward layers
decoder_ffn = Dense(latent_dim * 4, activation="relu")(decoder_cross_attention)
decoder_ffn = Dense(latent_dim)(decoder_ffn)
decoder_ffn = Add()([decoder_cross_attention, decoder_ffn])  # Residual connection
decoder_ffn = LayerNormalization()(decoder_ffn)

# Additional feed-forward block
decoder_ffn_2 = Dense(latent_dim * 4, activation="relu")(decoder_ffn)
decoder_ffn_2 = Dense(latent_dim)(decoder_ffn_2)
decoder_ffn_2 = Add()([decoder_ffn, decoder_ffn_2])  # Residual connection
decoder_ffn_2 = LayerNormalization()(decoder_ffn_2)

# Output layer
decoder_outputs = Dense(vocab_size, activation="softmax")(decoder_ffn_2)

def perplexity(y_true, y_pred):
    cross_entropy = tf.keras.losses.sparse_categorical_crossentropy(y_true, y_pred)
    return tf.exp(tf.reduce_mean(cross_entropy))

def exact_match(y_true, y_pred):
    # Reshape y_true to match the shape of the predicted classes
    y_true = tf.squeeze(y_true, axis=-1) # Remove the last dimension if present
    y_true = tf.cast(y_true, tf.int64)  
    y_pred_classes = tf.argmax(y_pred, axis=-1, output_type=tf.int64)  # Get predicted class indices

    # Ensure y_true and y_pred_classes have the same shape
    return tf.reduce_mean(tf.cast(tf.equal(y_true, y_pred_classes), tf.float32))

# Compile model
model = Model([encoder_inputs, decoder_inputs], decoder_outputs)
model.compile(optimizer="adam", loss="sparse_categorical_crossentropy", metrics=["accuracy", perplexity, exact_match])

# Prep train and test data -went with '42' for seed because it's the joke that keeps on giving
decoder_target_output = np.expand_dims(target_output_sequences, -1)
X_train, X_test, y_train, y_test, decoder_y_train, decoder_y_test = train_test_split(
    input_sequences, target_input_sequences, decoder_target_output, test_size=0.1, random_state=42
)


In [62]:
print("Num GPUs Available: ", len(tf.config.list_physical_devices('GPU')))

Num GPUs Available:  0


In [68]:
# Train the decoder model 

print("Training the decoder model")
model.fit(
    [X_train, y_train], decoder_y_train,
    validation_data=([X_test, y_test], decoder_y_test),
    batch_size=48, #48, #32,
    epochs=5, #50,
)

Training the decoder model
Epoch 1/5
48/48 ━━━━━━━━━━━━━━━━━━━━ 141s 3s/step - accuracy: 0.0859 - exact_match: 0.0859 - loss: 8.7522 - perplexity: 12974.6357 - val_accuracy: 0.1303 - val_exact_match: 0.1281 - val_loss: 6.7530 - val_perplexity: 881.3806
Epoch 2/5
48/48 ━━━━━━━━━━━━━━━━━━━━ 135s 3s/step - accuracy: 0.1625 - exact_match: 0.1626 - loss: 6.2782 - perplexity: 552.0728 - val_accuracy: 0.1940 - val_exact_match: 0.1952 - val_loss: 5.9963 - val_perplexity: 410.5519
Epoch 3/5
48/48 ━━━━━━━━━━━━━━━━━━━━ 136s 3s/step - accuracy: 0.2431 - exact_match: 0.2432 - loss: 5.3337 - perplexity: 209.8091 - val_accuracy: 0.2171 - val_exact_match: 0.2192 - val_loss: 5.7001 - val_perplexity: 307.7409
Epoch 4/5
48/48 ━━━━━━━━━━━━━━━━━━━━ 136s 3s/step - accuracy: 0.2829 - exact_match: 0.2829 - loss: 4.7471 - perplexity: 117.3480 - val_accuracy: 0.2319 - val_exact_match: 0.2341 - val_loss: 5.5414 - val_perplexity: 265.9081
Epoch 5/5
48/48 ━━━━━━━━━━━━━━━━━━━━ 136s 3s/step - accuracy: 0.3173 - exac

In [69]:
# Save the model because it takes forever to fit the damn thing (i.e. 30min to fit an <1sec to load a saved model)
model.save("/home/ec2-user/kaggle/rudolph/model_v2.keras")

In [ ]:
# Call saved model (note: keras file is too big to save on github so make sure to add in your .gitignore file)

#model = load_model("/home/ec2-user/kaggle/rudolph/model_v2.keras")

In [70]:
# inference
heads = 8
encoder_model = Model(encoder_inputs, encoder_outputs)

# Decoder for inference
decoder_inputs_inf = Input(shape=(max_seq_length - 1,))
decoder_embedding_inf = Embedding(vocab_size, embedding_dim)(decoder_inputs_inf)

decoder_self_attention_inf = MultiHeadAttention(num_heads=heads, key_dim=latent_dim)(decoder_embedding_inf, decoder_embedding_inf)
decoder_self_attention_inf = Add()([decoder_embedding_inf, decoder_self_attention_inf])
decoder_self_attention_inf = LayerNormalization()(decoder_self_attention_inf)

decoder_cross_attention_inf = MultiHeadAttention(num_heads=heads, key_dim=latent_dim)(decoder_self_attention_inf, encoder_outputs)
decoder_cross_attention_inf = Add()([decoder_self_attention_inf, decoder_cross_attention_inf])
decoder_cross_attention_inf = LayerNormalization()(decoder_cross_attention_inf)

decoder_ffn_inf = Dense(latent_dim * 4, activation="relu")(decoder_cross_attention_inf)
decoder_ffn_inf = Dense(latent_dim)(decoder_ffn_inf)
decoder_ffn_inf = Add()([decoder_cross_attention_inf, decoder_ffn_inf])
decoder_ffn_inf = LayerNormalization()(decoder_ffn_inf)

decoder_outputs_inf = Dense(vocab_size, activation="softmax")(decoder_ffn_inf)

decoder_model = Model([decoder_inputs_inf, encoder_outputs], decoder_outputs_inf)

In [72]:
#newest 
from collections import Counter
import numpy as np

def decode_sequence(input_seq, scrambled_sentence):
    """
    Decode a scrambled sentence while ensuring the output is a permutation
    of the words in the scrambled sentence and avoiding consecutive repetitions.
    I needed to mask words that are sampled outside the set of scrambled words 
    otherwise you end up with a lot of unwanted "extras". Also count down the words to 
    make sure you don't leave out dups (i.e. 'of' coming up 2x in input)
    """
    # Encode the input to get the context vector
    encoder_output = encoder_model.predict(input_seq)

    # Tokenize the scrambled sentence to get word counts
    scrambled_words = scrambled_sentence.split()
    word_count = Counter(scrambled_words)

    # Generate the initial target sequence with the start token
    target_seq = np.zeros((1, max_seq_length - 1))
    target_seq[0, 0] = tokenizer.word_index["<start>"]

    # Initialize variables for decoding
    stop_condition = False
    decoded_sentence = []

    while not stop_condition:
        # Predict the next token probabilities
        output_tokens = decoder_model.predict([target_seq, encoder_output])

        # Create a mask for valid words
        valid_word_indices = []
        for word, count in word_count.items():
            if count > 0:  # Only include words still available in scrambled input
                token_index = tokenizer.word_index.get(word, None)
                if token_index is not None:
                    valid_word_indices.append(token_index)

        # Mask out probabilities of words that are not in the scrambled set
        if valid_word_indices:
            mask = np.ones(output_tokens[0, -1, :].shape, dtype=bool)
            mask[valid_word_indices] = False  # Only allow valid word indices
            output_tokens[0, -1, mask] = 0
        else:
            # No valid words left, terminate decoding
            stop_condition = True
            continue

        # Resample a valid word, avoiding consecutive repetitions
        sorted_indices = output_tokens[0, -1, :].argsort()[::-1]  # Sort probabilities in descending order
        sampled_word = None
        for token_index in sorted_indices:
            word_candidate = tokenizer.index_word.get(token_index, None)
            if (
                word_candidate in word_count and
                word_count[word_candidate] > 0 and
                (not decoded_sentence or word_candidate != decoded_sentence[-1])  # Avoid consecutive repetition
            ):
                sampled_word = word_candidate
                break

        # If no valid word is found, terminate
        if sampled_word is None:
            stop_condition = True
            continue

        # Add the sampled word to the decoded sentence
        decoded_sentence.append(sampled_word)
        word_count[sampled_word] -= 1

        # Debugging prints
        print(f"Resampled token index: {token_index}")
        print(f"Resampled word: {sampled_word}")

        # Check if decoding is complete
        if sum(word_count.values()) == 0:
            stop_condition = True

        # Update the target sequence for the next iteration
        target_seq = np.zeros((1, max_seq_length - 1))
        target_seq[0, 0] = token_index

    # Ensure all words are included
    missing_words = []
    for word, count in word_count.items():
        if count > 0:
            missing_words.extend([word] * count)
    decoded_sentence.extend(missing_words)

    return " ".join(decoded_sentence).strip()


In [ ]:
"""
# toss together some tests
scrambled_input = "row your boat down the stream gently row row"
#scrambled_input ="on the sat mat cat the"
#scrambled_input ="are ? you where"

input_sequence = pad_sequences(tokenizer.texts_to_sequences([scrambled_input]), maxlen=max_seq_length, padding="post")
unscrambled_sentence = decode_sequence(input_sequence, scrambled_input)
print(f"Scrambled: {scrambled_input}")
print(f"Unscrambled: {unscrambled_sentence}")
"""

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 170ms/step


2024-12-05 14:57:51.799355: W external/local_xla/xla/tsl/framework/cpu_allocator_impl.cc:83] Allocation of 1408951296 exceeds 10% of free system memory.
2024-12-05 14:57:54.234182: W external/local_xla/xla/tsl/framework/cpu_allocator_impl.cc:83] Allocation of 1409101440 exceeds 10% of free system memory.


1/1 ━━━━━━━━━━━━━━━━━━━━ 5s 5s/step
Resampled token index: 984
Resampled word: row


2024-12-05 14:57:57.248273: W external/local_xla/xla/tsl/framework/cpu_allocator_impl.cc:83] Allocation of 1408951296 exceeds 10% of free system memory.
2024-12-05 14:57:59.659241: W external/local_xla/xla/tsl/framework/cpu_allocator_impl.cc:83] Allocation of 1409101440 exceeds 10% of free system memory.


1/1 ━━━━━━━━━━━━━━━━━━━━ 5s 5s/step
Resampled token index: 61
Resampled word: your


2024-12-05 14:58:02.682114: W external/local_xla/xla/tsl/framework/cpu_allocator_impl.cc:83] Allocation of 1408951296 exceeds 10% of free system memory.


1/1 ━━━━━━━━━━━━━━━━━━━━ 5s 5s/step
Resampled token index: 984
Resampled word: row
1/1 ━━━━━━━━━━━━━━━━━━━━ 5s 5s/step
Resampled token index: 978
Resampled word: gently
1/1 ━━━━━━━━━━━━━━━━━━━━ 5s 5s/step
Resampled token index: 984
Resampled word: row
1/1 ━━━━━━━━━━━━━━━━━━━━ 5s 5s/step
Resampled token index: 46
Resampled word: down
1/1 ━━━━━━━━━━━━━━━━━━━━ 5s 5s/step
Resampled token index: 1
Resampled word: the
1/1 ━━━━━━━━━━━━━━━━━━━━ 5s 5s/step
Resampled token index: 3853
Resampled word: boat
1/1 ━━━━━━━━━━━━━━━━━━━━ 5s 5s/step
Scrambled: row your boat down the stream gently row row
Unscrambled: row your row gently row down the boat stream


In [ ]:
"""
text_0 = "advent chimney elf family fireplace gingerbread mistletoe ornament reindeer scrooge"
text_1 = "advent chimney elf family fireplace gingerbread mistletoe ornament reindeer scrooge walk give jump drive bake the sleep night laugh and"
text_2 = "yuletide decorations gifts cheer holiday carol magi nutcracker polar grinch sleigh chimney workshop stocking ornament holly jingle beard naughty nice"
text_3 = "yuletide decorations gifts cheer holiday carol magi nutcracker polar grinch sleigh chimney workshop stocking ornament holly jingle beard naughty nice sing cheer and of the is eat visit relax unwrap"
text_4 = "hohoho candle poinsettia snowglobe peppermint eggnog fruitcake chocolate candy puzzle game doll toy workshop wonder believe dream hope peace joy merry season greeting card wrapping paper bow fireplace night cookie milk star wish wreath angel the to of and in that have it not with as you from we kaggle"
text_5 = "advent chimney elf family fireplace gingerbread mistletoe ornament reindeer scrooge walk give jump drive bake the sleep night laugh and yuletide decorations gifts cheer holiday carol magi nutcracker polar grinch sleigh chimney workshop stocking ornament holly jingle beard naughty nice sing cheer and of the is eat visit relax unwrap hohoho candle poinsettia snowglobe peppermint eggnog fruitcake chocolate candy puzzle game doll toy workshop wonder believe dream hope peace joy merry season greeting card wrapping paper bow fireplace night cookie milk star wish wreath angel the to of and in that have it not with as you from we kaggle"
scrambled_input = text_1
input_sequence = pad_sequences(tokenizer.texts_to_sequences([scrambled_input]), maxlen=max_seq_length, padding="post")
unscrambled_sentence = decode_sequence(input_sequence, scrambled_input)
print(f"Scrambled: {scrambled_input}")
print(f"Unscrambled: {unscrambled_sentence}")
"""

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 28ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 463ms/step
Resampled token index: 4277
Resampled word: reindeer
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 429ms/step
Resampled token index: 821
Resampled word: walk
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 443ms/step
Resampled token index: 226
Resampled word: night
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 439ms/step
Resampled token index: 669
Resampled word: sleep
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 437ms/step
Resampled token index: 878
Resampled word: laugh
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 433ms/step
Resampled token index: 154
Resampled word: give
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 435ms/step
Resampled token index: 3862
Resampled word: ornament
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 439ms/step
Resampled token index: 1842
Resampled word: family
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 435ms/step
Resampled token index: 1
Resampled word: the
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 429ms/step
Resampled token index: 2
Resampled word: and
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 427ms/step
Scrambled: advent chimney elf family firepl

In [15]:
csv_file = "/home/ec2-user/kaggle/rudolph/sample_submission.csv"
input = pd.read_csv(csv_file)
input = input.drop(columns=['id'])


In [16]:

# Loop through each row in column 'text'
for index, value in input['text'].items():
    # Create a variable for the string in column 'XX'
    current_string = value
    print(f"Row {index}: {current_string}")

Row 0: advent chimney elf family fireplace gingerbread mistletoe ornament reindeer scrooge
Row 1: advent chimney elf family fireplace gingerbread mistletoe ornament reindeer scrooge walk give jump drive bake the sleep night laugh and
Row 2: yuletide decorations gifts cheer holiday carol magi nutcracker polar grinch sleigh chimney workshop stocking ornament holly jingle beard naughty nice
Row 3: yuletide decorations gifts cheer holiday carol magi nutcracker polar grinch sleigh chimney workshop stocking ornament holly jingle beard naughty nice sing cheer and of the is eat visit relax unwrap
Row 4: hohoho candle poinsettia snowglobe peppermint eggnog fruitcake chocolate candy puzzle game doll toy workshop wonder believe dream hope peace joy merry season greeting card wrapping paper bow fireplace night cookie milk star wish wreath angel the to of and in that have it not with as you from we kaggle
Row 5: advent chimney elf family fireplace gingerbread mistletoe ornament reindeer scrooge wal

In [73]:
output_file = []
for index, value in input['text'].items():
    # Create a variable for the string in column 'text'
    scrambled_input = value
    #print(f"Row {index}: {current_string}")

    input_sequence = pad_sequences(tokenizer.texts_to_sequences([scrambled_input]), maxlen=max_seq_length, padding="post")
    unscrambled_sentence = decode_sequence(input_sequence, scrambled_input)
    output_file.append(unscrambled_sentence)
    print(f"Scrambled: {scrambled_input}")
    print(f"Unscrambled: {unscrambled_sentence}")

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 87ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 210ms/step
Resampled token index: 19279
Resampled word: ornament
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 48ms/step
Resampled token index: 33850
Resampled word: fireplace
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 47ms/step
Resampled token index: 14260
Resampled word: advent
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 47ms/step
Resampled token index: 8796
Resampled word: chimney
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 48ms/step
Resampled token index: 446
Resampled word: family
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 48ms/step
Resampled token index: 25106
Resampled word: reindeer
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 48ms/step
Scrambled: advent chimney elf family fireplace gingerbread mistletoe ornament reindeer scrooge
Unscrambled: ornament fireplace advent chimney family reindeer elf gingerbread mistletoe scrooge
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 48ms/step
Resampled token index: 19279
Resampled word: ornament
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 61ms/step
Resampled token in

In [74]:
unscrambled = pd.DataFrame(output_file, columns=["text"])

# Display the DataFrame
#print(input)
#print(unscrambled)
#print(output_file)
#print(max_seq_length)
 # Check that each submitted string is a permutation of the solution string
sol_counts = unscrambled.loc[:, 'text'].str.split().apply(Counter)

print(f"solution counts = {sol_counts}")
sub_counts = input.loc[:, 'text'].str.split().apply(Counter)

print(f"input counts = {sub_counts}")
invalid_mask = sol_counts != sub_counts

if invalid_mask.any():
    raise ParticipantVisibleError(
        'At least one submitted string is not a valid permutation of the solution string.'
    )

print(invalid_mask)


solution counts = 0    {'ornament': 1, 'fireplace': 1, 'advent': 1, '...
1    {'ornament': 1, 'walk': 1, 'sleep': 1, 'give':...
2    {'ornament': 1, 'holiday': 1, 'carol': 1, 'hol...
3    {'ornament': 1, 'sing': 1, 'holiday': 1, 'caro...
4    {'have': 1, 'candy': 1, 'doll': 1, 'bow': 1, '...
5    {'ornament': 2, 'sing': 1, 'walk': 1, 'have': ...
Name: text, dtype: object
input counts = 0    {'advent': 1, 'chimney': 1, 'elf': 1, 'family'...
1    {'advent': 1, 'chimney': 1, 'elf': 1, 'family'...
2    {'yuletide': 1, 'decorations': 1, 'gifts': 1, ...
3    {'yuletide': 1, 'decorations': 1, 'gifts': 1, ...
4    {'hohoho': 1, 'candle': 1, 'poinsettia': 1, 's...
5    {'advent': 1, 'chimney': 2, 'elf': 1, 'family'...
Name: text, dtype: object
0    False
1    False
2    False
3    False
4    False
5    False
Name: text, dtype: bool


In [54]:
print(invalid_mask)

0    False
1    False
2    False
3    False
4    False
5    False
Name: text, dtype: bool


In [19]:
# Calculate Perpexity using kaggle's competition script 
%run '/home/ec2-user/kaggle/rudolph/perplexityCalc.py'

/home/ec2-user/.local/lib/python3.9/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [20]:

model_path = "/home/ec2-user/.cache/kagglehub/models/google/gemma-2/transformers/gemma-2-9b/2"
#score(unscrambled, input, 'text', model_path=model_path, clear_mem=True) > 0

In [ ]:
#scores = score(unscrambled, input, 'text', model_path=model_path, clear_mem=True)

Loading checkpoint shards: 100%|██████████| 8/8 [00:01<00:00,  4.46it/s]


In [ ]:
#print(scores)
# Score1 = 2174.8712132759915

2174.8712132759915


In [21]:
perplex = PerplexityCalculator(model_path=model_path)

Loading checkpoint shards: 100%|██████████| 8/8 [00:02<00:00,  2.69it/s]


In [18]:
perplex.get_perplexity(unscrambled["text"].tolist())

[9903.226408462264,
 10963.900647623153,
 6344.4446716903585,
 5000.990165118489,
 1680.6263738430855,
 875.5237118216133]

In [27]:
#inc attention heads to 8
perplex.get_perplexity(unscrambled["text"].tolist())

[3216.066741168979,
 4528.651590492278,
 9355.963853324018,
 5685.485737472906,
 1626.8518194435935,
 1010.1458623209938]

In [36]:
#inc attention heads to 12
perplex.get_perplexity(unscrambled["text"].tolist())

[7896.911017907184,
 9243.666007673444,
 5403.225440491761,
 5721.859189184384,
 2094.5395112919346,
 948.2182468060116]

In [33]:
perplex.get_perplexity(input["text"].tolist())

[3877.722785267886,
 6059.756959306958,
 1116.90819498697,
 1286.9573745451812,
 352.73848538785325,
 355.14348016109784]

In [ ]:
#inc attention heads to 8 and emb_dim to 120
perplex.get_perplexity(unscrambled["text"].tolist())

[2425.535264300109,
 15160.008295000938,
 7304.855871041513,
 5593.818453433429,
 1743.8614786236003,
 843.2115732946356]

In [ ]:
#inc attention heads to 8 and emb_dim to 150 no modelfit
perplex.get_perplexity(unscrambled["text"].tolist())

[3404.584904538774,
 8749.373736945034,
 4373.596011237068,
 4049.9870542866615,
 1166.3567289365546,
 841.3704761685888]

In [ ]:
#inc attention heads to 8 and emb_dim to 150 with modelfit inf heads 8
perplex.get_perplexity(unscrambled["text"].tolist())

[10172.475119820328,
 10721.337031147717,
 4254.347491127482,
 3337.1139756777548,
 2463.133986724227,
 962.7689370312606]

In [65]:
#inc attention heads to 8 and emb_dim to 150 with modelfit inf heads 4
perplex.get_perplexity(unscrambled["text"].tolist())

[3367.289392659192,
 9122.461860523645,
 5947.483210304593,
 5399.815285804229,
 2285.876228686109,
 794.3753145400831]

In [ ]:
#inc attention heads to 8 and emb_dim to 150 with modelfit inf heads 4 max length = 750
# this took forever because of the max length and didn't improve at all!
perplex.get_perplexity(unscrambled["text"].tolist())

[3367.289392659192,
 9122.461860523645,
 5947.483210304593,
 5399.815285804229,
 2403.1356537498855,
 814.2893806766322]

In [89]:
#inc attention heads to 8 and emb_dim to 175 with modelfit infer heads 4 and positional encoding
# 
perplex.get_perplexity(unscrambled["text"].tolist())

[12346.834283670743,
 5106.185912901053,
 10242.574088130088,
 6117.747902121899,
 1858.6124736937193,
 921.2362292674757]

In [100]:
#inc attention heads to 8 and emb_dim to 175 with modelfit infer heads 4 and positional encoding
# Perplexity optimized
perplex.get_perplexity(unscrambled["text"].tolist())

[3398.829835345036,
 13343.6957527574,
 3439.5927884843472,
 3320.248012423757,
 1405.1161025533756,
 982.2499898287296]

In [19]:
#inc attention heads to 8 and emb_dim to 150 with modelfit infer heads 4 and positional encoding
# Epocs from 50 to 70, batches from 32 to 48
# Perplexity optimized
perplex.get_perplexity(unscrambled["text"].tolist())

[4017.3126135779607,
 6345.0981630085535,
 3524.4796881204325,
 2393.302195973814,
 1280.9122481510972,
 826.9844031275601]

In [22]:
#inc attention heads to 8 and emb_dim to 150 with modelfit infer heads 4 and positional encoding
# Epocs from 50 to 70, batches from 32 to 48, max length 1000 (so far 1500 and up runs out of resources)
# Perplexity optimized
perplex.get_perplexity(unscrambled["text"].tolist())

[5059.974033526428,
 7550.261682120035,
 3188.45038839725,
 3007.861276239668,
 2241.5789380002225,
 1046.2160989181912]

In [22]:
#inc attention heads to 8 and emb_dim to 175 with modelfit infer heads 4 and positional encoding
# Epocs 10, batches 64, max length 75
# stories segmented with length 75
# Perplexity optimized
perplex.get_perplexity(unscrambled["text"].tolist())

[6125.833800613256,
 6332.439683590543,
 6288.573433470001,
 5525.854759633294,
 1723.7445981924384,
 825.4475247582338]

In [59]:
#inc attention heads to 8 and emb_dim to 150 with modelfit infer heads 8 and positional encoding
# Epocs 5, batches 48, max length 150
# stories segmented with length 150
# Perplexity optimized
perplex.get_perplexity(unscrambled["text"].tolist())

[7821.353972500294,
 4901.57368186373,
 3550.970938500076,
 3605.5561989531957,
 1905.7717915374674,
 922.98490204875]

In [75]:
#inc attention heads to 8 and emb_dim to 256 with modelfit infer heads 8 and positional encoding
# Epocs 5, batches 48, max length 150
# stories segmented with length 200
# Perplexity and exact_match optimized
perplex.get_perplexity(unscrambled["text"].tolist())

[2497.828068886327,
 6147.593097697407,
 1678.252746167442,
 2487.349748070276,
 1708.3887763117932,
 700.1504779608912]

In [19]:
perplex.get_perplexity(input["text"].tolist())

[3877.722785267886,
 6059.76273834429,
 1116.9087275704267,
 1286.9573745451812,
 352.7381489903797,
 355.14348016109784]